In [1]:
%pip install sec-edgar-downloader
%pip install investpy
%pip install PyPDF2
%pip install aiohttp aiofiles beautifulsoup4 PyPDF2 langchain
%pip install aiolimiter
%pip install nest_asyncio
%pip install tqdm
%pip install nltk langdetect
%pip install yfinance
%pip install ftfy
%pip install aiofiles
%pip install nltk
!python -m nltk.downloader punkt


Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 25.0.1 -> 25.1.1
[notice] To update, run: python.exe -m pip install --upgrade pip


Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 25.0.1 -> 25.1.1
[notice] To update, run: python.exe -m pip install --upgrade pip


Note: you may need to restart the kernel to use updated packages.


...


[notice] A new release of pip is available: 25.0.1 -> 25.1.1
[notice] To update, run: python.exe -m pip install --upgrade pip


Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 25.0.1 -> 25.1.1
[notice] To update, run: python.exe -m pip install --upgrade pip


Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 25.0.1 -> 25.1.1
[notice] To update, run: python.exe -m pip install --upgrade pip
<frozen runpy>:128: RuntimeWarning: 'nltk.downloader' found in sys.modules after import of package 'nltk', but prior to execution of 'nltk.downloader'; this may result in unpredictable behaviour
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\Serban\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [2]:
import pandas as pd
import yfinance as yf
import os
import time
from datetime import datetime
import random
import logging
import pickle
from concurrent.futures import ThreadPoolExecutor, as_completed
from tenacity import retry, stop_after_attempt, wait_exponential
from pydantic import BaseModel, ValidationError
import pyarrow.parquet as pq
from tqdm import tqdm
from bs4 import BeautifulSoup
import requests
from io import StringIO, BytesIO
import investpy
import json
from typing import List, Dict, Optional
import gzip
import sqlite3
from datetime import datetime, timedelta
import re
from PyPDF2 import PdfReader
from langchain.text_splitter import RecursiveCharacterTextSplitter
from dateutil import parser


In [4]:
#maybe consider FTSE100
#don t forget about cryptos and forex

def get_sp500_tickers():
    """Get S&P 500 tickers with more reliable table parsing"""
    url = 'https://en.wikipedia.org/wiki/List_of_S%26P_500_companies'
    response = requests.get(url)
    soup = BeautifulSoup(response.text, 'html.parser')
    table = soup.find('table', {'id': 'constituents'})
    df = pd.read_html(StringIO(str(table)))[0]
    return df['Symbol'].tolist()

def get_nasdaq_tickers():
    """Get NASDAQ-listed common stocks with proper column handling"""
    url = "https://www.nasdaqtrader.com/dynamic/SymDir/nasdaqlisted.txt"
    columns = [
        'Symbol', 'Security Name', 'Market Category', 'Test Issue',
        'Financial Status', 'Round Lot Size', 'ETF', 'NextShares'
    ]
    df = pd.read_csv(url, sep="|", names=columns)
    df = df[:-1]  # Remove summary row
    # Filter out ETFs and test issues
    df = df[(df['Test Issue'] == 'N') & (df['ETF'] == 'N')]
    return df['Symbol'].tolist()

def get_other_tickers():
    """Get NYSE/AMEX stocks with proper column handling"""
    url = "https://www.nasdaqtrader.com/dynamic/SymDir/otherlisted.txt"
    columns = [
        'ACT Symbol', 'Security Name', 'Exchange', 'CQS Symbol',
        'ETF', 'Round Lot Size', 'Test Issue', 'NASDAQ Symbol'
    ]
    df = pd.read_csv(url, sep="|", names=columns)
    df = df[:-1]  # Remove summary row
    # Filter out ETFs and test issues
    df = df[(df['Test Issue'] == 'N') & (df['ETF'] == 'N')]
    return df['ACT Symbol'].tolist()

def get_global_tickers():
    """Get global tickers with error handling"""
    try:
        stocks_df = investpy.stocks.get_stocks()
        # Filter for common stock types (adjust based on available data)
        if 'type' in stocks_df.columns:
            stocks_df = stocks_df[stocks_df['type'] == 'Stock']
        return stocks_df['symbol'].unique().tolist()
    except ImportError:
        print("Global tickers disabled: install investpy (pip install investpy)")
        return []
    except Exception as e:
        print(f"Error fetching global tickers: {str(e)}")
        return []

def get_all_tickers():
    """Combine all sources with error handling"""
    tickers = []

    try:
        tickers += get_sp500_tickers()
        print(f"Found {len(tickers)} S&P 500 tickers")
    except Exception as e:
        print(f"Error fetching S&P 500: {str(e)}")

    try:
        nasdaq = get_nasdaq_tickers()
        tickers += nasdaq
        print(f"Added {len(nasdaq)} NASDAQ tickers")
    except Exception as e:
        print(f"Error fetching NASDAQ: {str(e)}")

    try:
        other = get_other_tickers()
        tickers += other
        print(f"Added {len(other)} NYSE/AMEX tickers")
    except Exception as e:
        print(f"Error fetching NYSE/AMEX: {str(e)}")

    try:
        global_tickers = get_global_tickers()
        tickers += global_tickers
        print(f"Added {len(global_tickers)} global tickers")
    except Exception as e:
        print(f"Error fetching global tickers: {str(e)}")

    # Clean and deduplicate
    clean_tickers = list(set([t.strip().upper() for t in tickers if isinstance(t, str)]))
    return sorted(clean_tickers)



In [ ]:
if __name__ == "__main__":
    all_tickers = get_all_tickers()
    print(f"\nTotal unique tickers: {len(all_tickers)}")



    #!!! separate the global tickers from the important markets so that the code for the filings are done on the important markets



    # Save to file
    # with open("all_tickers.txt", "w") as f:
    #     f.write("\n".join(all_tickers))

    #store_historical_data()



Found 503 S&P 500 tickers
Added 4002 NASDAQ tickers
Added 3158 NYSE/AMEX tickers
Global tickers disabled: install investpy (pip install investpy)
Added 0 global tickers

Total unique tickers: 7159


**The above code works well for retrieving sec filings, whena query is prompted, the model will call the retriver for the sec filings which will be stored in a database either loccal or on the cloud if the sec filings is what is needed, or it will either call the api for the stock price or the api for the analytics- Finnhub**

In [ ]:
# --- Test Execution ---
if __name__ == "__main__":
    filings = fetch_sec_filings("AAPL", filing_type='10-Q' ,max_results=1,save_to_disk=False)
    print(filings)
    print(filings[0]['documents'][0]['text'][2])



In [7]:
import os, re, json, time, asyncio, aiofiles
from io import BytesIO
from typing import List
from bs4 import BeautifulSoup
from PyPDF2 import PdfReader
import aiohttp
from langchain.text_splitter import RecursiveCharacterTextSplitter

# --- CONFIG ---
HEADERS = {
    "User-Agent": "University_Project_Financial_LLM (muie.restante@gmail.com)",
    "Accept-Encoding": "gzip, deflate",
    "Host": "www.sec.gov"
}
SEC_BASE = "https://www.sec.gov"
CIK_LOOKUP = f"{SEC_BASE}/files/company_tickers.json"
SEARCH_URL = f"{SEC_BASE}/cgi-bin/browse-edgar"
DATA_DIR = "sec_filings_second"
DELAY = 1.0
CHUNK_SIZE = 1000
CHUNK_OVERLAP = 200
MAX_CONCURRENT_REQUESTS = 5

# --- UTILS ---
async def async_get(session, url, semaphore, retries=3):
    for attempt in range(retries):
        async with semaphore:
            try:
                async with session.get(url, headers=HEADERS, timeout=aiohttp.ClientTimeout(total=30)) as resp:
                    await asyncio.sleep(DELAY)
                    if resp.status == 429:
                        wait_time = 2 ** (attempt + 5)
                        print(f"Rate limited. Retrying in {wait_time}s...")
                        await asyncio.sleep(wait_time)
                        continue
                    content_type = resp.headers.get("Content-Type", "")
                    if "application/json" not in content_type and url.endswith(".json"):
                        print(f"Unexpected content type: {content_type}")
                        return None
                    return await resp.read()
            except Exception as e:
                print(f"Request failed (attempt {attempt+1}): {e}")
                if attempt == retries - 1:
                    return None
                await asyncio.sleep(2 ** (attempt + 1))
    return None

async def download_cik_lookup(session):
    try:
        async with session.get(CIK_LOOKUP, headers=HEADERS) as resp:
            await asyncio.sleep(DELAY)
            if resp.status != 200:
                raise Exception(f"Status {resp.status}")
            content_type = resp.headers.get("Content-Type", "")
            if "application/json" not in content_type:
                raise Exception(f"Unexpected content-type: {content_type}")
            return await resp.json()
    except Exception as e:
        print(f"Failed to fetch CIK lookup: {e}")
        return {}

def get_cik_from_lookup(ticker: str, lookup_data: dict) -> str:
    for entry in lookup_data.values():
        if entry["ticker"].lower() == ticker.lower():
            return str(entry["cik_str"]).zfill(10)
    return None

def split_text(text: str) -> List[str]:
    splitter = RecursiveCharacterTextSplitter(
        chunk_size=CHUNK_SIZE,
        chunk_overlap=CHUNK_OVERLAP,
        separators=["\n\n", "\n", ".", " ", ""]
    )
    return splitter.split_text(text)

def clean_text(text: str) -> str:
    text = re.sub(r'http[s]?://\S+', '', text)
    text = re.sub(r"UNITED STATES SECURITIES.*?Washington, D\.C\.\s*\d+", "", text, flags=re.DOTALL)
    text = re.sub(r"Table of Contents.*?(?=Item\s+1)", "", text, flags=re.DOTALL | re.IGNORECASE)
    text = re.sub(r'[0-9]{10,}', '', text)
    text = re.sub(r'[a-fA-F0-9]{32,}', '', text)
    return re.sub(r'\n+', '\n', text.replace("\xa0", " ")).strip()

async def get_filing_urls(session, cik: str, filing_type: str, max_docs=5):
    try:
        params = {
            "action": "getcompany",
            "CIK": cik,
            "type": filing_type,
            "owner": "exclude",
            "count": "100"
        }
        async with session.get(SEARCH_URL, params=params, headers=HEADERS) as resp:
            content = await resp.text()
            soup = BeautifulSoup(content, "html.parser")
            table = soup.find("table", class_="tableFile2")
            filings = []
            if table:
                rows = table.find_all("tr")[1:]
                for row in rows:
                    cols = row.find_all("td")
                    if len(cols) >= 4:
                        link = cols[1].find("a")
                        date = cols[3].text.strip()
                        if link:
                            filings.append({
                                "detail_url": f"{SEC_BASE}{link['href']}",
                                "date": date
                            })
                        if len(filings) >= max_docs:
                            break
            return filings
    except Exception as e:
        print(f"Error fetching filings for CIK {cik}: {e}")
        return []

async def extract_text_from_doc(session, doc_url: str, semaphore) -> str:
    raw = await async_get(session, doc_url, semaphore)
    if not raw:
        return ""
    try:
        if doc_url.endswith(".pdf"):
            reader = PdfReader(BytesIO(raw))
            text = "\n".join(p.extract_text() or "" for p in reader.pages)
        else:
            soup = BeautifulSoup(raw, "html.parser")
            text = soup.get_text()
        return clean_text(text)
    except Exception as e:
        print(f"Error extracting text from {doc_url}: {e}")
        return ""

async def process_filing(session, filing, ticker, filing_type, semaphore):
    try:
        raw = await async_get(session, filing["detail_url"], semaphore)
        if not raw:
            return None
        soup = BeautifulSoup(raw, "html.parser")
        table = soup.find("table", class_="tableFile")
        if not table:
            return None
        for row in table.find_all("tr")[1:]:
            cols = row.find_all("td")
            if len(cols) >= 4:
                doc_type = cols[3].text.strip().lower()
                href = cols[2].find("a")
                if not href:
                    continue
                href = href["href"]
                filename = href.split("/")[-1].lower()
                if(
                    doc_type == filing_type.lower() and
                    (filename.endswith(".htm") or filename.endswith(".html"))
                    and not any(x in filename for x in ["xbrl", "xml", "ex-99", "exhibit", "form", "index"])
                ):
                    doc_url = f"{SEC_BASE}{href}".replace("/ix?doc=", "") # Corrected line
                    text = await extract_text_from_doc(session, doc_url, semaphore)
                    if not text:
                        continue
                    return {
                        "ticker": ticker,
                        "date": filing["date"],
                        "text": text,
                        "url": doc_url,
                        "filing_type": filing_type
                    }
                        
                    
        return None
    except Exception as e:
        print(f"Error processing filing {filing['detail_url']}: {e}")
        return None

async def process_company(session, ticker, cik, semaphore, filing_type="10-K", max_docs=5):
    filing_dir = os.path.join(DATA_DIR, ticker, filing_type)
    if os.path.exists(filing_dir) and os.listdir(filing_dir):
        print(f"Skipping existing: {ticker} {filing_type}")
        return

    filings = await get_filing_urls(session, cik, filing_type, max_docs)
    if not filings:
        print(f"No filings found for {ticker} {filing_type}")
        return

    for filing in filings:
        path = os.path.join(DATA_DIR, ticker, filing_type, f"{filing['date']}.json")
        if os.path.exists(path):
            continue
        doc = await process_filing(session, filing, ticker, filing_type, semaphore)
        if doc:
            os.makedirs(os.path.dirname(path), exist_ok=True)
            async with aiofiles.open(path, "w") as f:
                await f.write(json.dumps(doc))

async def run_pipeline(tickers):
    semaphore = asyncio.Semaphore(MAX_CONCURRENT_REQUESTS)
    async with aiohttp.ClientSession() as session:
        cik_lookup = await download_cik_lookup(session)
        if not cik_lookup:
            print("Aborting: Failed to fetch CIK lookup")
            return

        BATCH_SIZE = 50
        for i in range(0, len(tickers), BATCH_SIZE):
            batch = tickers[i:i+BATCH_SIZE]
            print(f"Processing batch {i//BATCH_SIZE + 1}/{(len(tickers)//BATCH_SIZE)+1}")
            tasks = []
            for ticker in batch:
                cik = get_cik_from_lookup(ticker, cik_lookup)
                if not cik:
                    print(f"CIK not found: {ticker}")
                    continue
                tasks.append(process_company(session, ticker, cik, semaphore, "10-K", 5))
                tasks.append(process_company(session, ticker, cik, semaphore, "10-Q", 15))
            await asyncio.gather(*tasks)
            print(f"Finished batch {i//BATCH_SIZE + 1}")




tickers = get_sp500_tickers() + get_nasdaq_tickers() + get_other_tickers()



In [ ]:
print(tickers.__len__())

7637


In [8]:
import nest_asyncio
nest_asyncio.apply()
await run_pipeline(tickers[:10])

Processing batch 1/1
Finished batch 1


In [17]:
import pickle
import os
import pandas as pd

file = "earnings_transcripts/motley-fool-data.pkl"
#find entry with ticker name ABM, year 2021, quarter 2
#inspect the file
if os.path.exists(file):
    with open(file, "rb") as f:
        data = pickle.load(f)
    df = pd.DataFrame(data)
    print(df.head())
    # Example: Find entry with ticker 'ABM', year 2021, quarter 2
    result = df[(df['ticker'] == 'ABM') & (df['date'] == "Jun 9, 2021, 8:30 a.m. ET") & (df['q'] == "2021-Q2")]
    if not result.empty:
        print("Found entry:")
        with open("abm_2021_q2.txt", "w") as f:
            #write the whole result to a text file
            f.write(result.to_string(index=False))
        print(result.to_string(index=False))
    else:
        print("No entry found for ABM, 2021, Q2")




                         date      exchange        q ticker  \
0  Aug 27, 2020, 9:00 p.m. ET  NASDAQ: BILI  2020-Q2   BILI   
1  Jul 30, 2020, 4:30 p.m. ET     NYSE: GFF  2020-Q3    GFF   
2  Oct 23, 2019, 5:00 p.m. ET  NASDAQ: LRCX  2020-Q1   LRCX   
3  Nov 6, 2019, 12:00 p.m. ET  NASDAQ: BBSI  2019-Q3   BBSI   
4   Aug 7, 2019, 8:30 a.m. ET  NASDAQ: CSTE  2019-Q2   CSTE   

                                          transcript  
0  Prepared Remarks:\nOperator\nGood day, and wel...  
1  Prepared Remarks:\nOperator\nThank you for sta...  
2  Prepared Remarks:\nOperator\nGood day and welc...  
3  Prepared Remarks:\nOperator\nGood day, everyon...  
4  Prepared Remarks:\nOperator\nGreetings and wel...  
Found entry:
                     date  exchange       q ticker                                                                                                                                                                                                                                    

In [ ]:
import re
import ftfy
import nltk
from nltk.tokenize import sent_tokenize
import logging
import os
import json
import pandas as pd # Added for DataFrame processing

# --- NLTK Setup ---
try:
    nltk.data.find('tokenizers/punkt')
except (nltk.downloader.DownloadError, LookupError):
    logging.info("NLTK 'punkt' model not found or outdated. Downloading/Updating...")
    nltk.download('punkt', quiet=True)

logging.basicConfig(level=logging.INFO, format='%(asctime)s - %(levelname)s - %(message)s')

# --- Text Cleaning Utilities (Identical to previous version) ---
def normalize_text_generic(text: str) -> str:
    if not text: return ""
    text = ftfy.fix_text(text)
    replacements = {'\u201c': '"', '\u201d': '"', '\u2018': "'", '\u2019': "'",
                    '\u2022': '* ', '\u2013': '-', '\u2014': '--', '\u00A0': ' ', '�': "'"}
    for unicode_char, replacement in replacements.items():
        text = text.replace(unicode_char, replacement)
    return text

def clean_speech_text(text: str) -> str:
    if not text: return ""
    text = re.sub(r'[ \t]{2,}', ' ', text)
    noise_patterns = [
        r'\[Operator Instructions\]', r'\[Technical Issues\]', r'\[Phonetic\]',
        r'\[Indecipherable\]', r'\[Speech Overlap\]', r'\[Foreign Speech\]',
        r'Sir, please go ahead\.', r'Please go ahead\.',
        r'Today\'s conference is being recorded\.',
        r'\(Operator Instructions\)'
    ]
    for pattern_str in noise_patterns:
        text = re.sub(pattern_str, '', text, flags=re.IGNORECASE)
    return text.strip()

def sentence_segment_and_filter(text: str, min_sentence_words: int = 2) -> str:
    if not text: return ""
    text_single_line = re.sub(r'\s*\n\s*', ' ', text).strip()
    if not text_single_line: return ""

    try:
        sents_original = sent_tokenize(text_single_line)
    except Exception:
        sents_original = [s.strip() for s in re.split(r'(?<=[.!?])\s+', text_single_line) if s.strip()]

    valid_sentences = []
    seen_sentences_norm = set()
    for s in sents_original:
        s_stripped = s.strip()
        if not s_stripped: continue
        norm_s = re.sub(r'\s+', ' ', s_stripped).lower()
        if len(s_stripped.split()) >= min_sentence_words and norm_s not in seen_sentences_norm:
            valid_sentences.append(s_stripped)
            seen_sentences_norm.add(norm_s)
    return ' '.join(valid_sentences)

# --- Transcript Processing Logic ---
def is_potential_speaker_line_with_titles(line: str, participant_list_full: list = None) -> str | None:
    # (Identical to previous version, ensuring it returns the full speaker string with title)
    line_stripped = line.strip()
    if not line_stripped or len(line_stripped) > 150:
        return None

    if participant_list_full:
        sorted_participants_full = sorted(participant_list_full, key=len, reverse=True)
        for p_full_string in sorted_participants_full:
            if re.fullmatch(re.escape(p_full_string) + r":?", line_stripped, re.IGNORECASE):
                return p_full_string.rstrip(':')
            if line_stripped.lower().startswith(p_full_string.lower() + ":"):
                 return p_full_string

    match = re.fullmatch(r"([\w\s\.'-]+?)\s*--\s*([\w\s,&'\.-]+(?:Relations|Officer|Analyst|Operator|Moderator|Host|Chairman|Chairwoman)?[\w\s,\.'-]*)$", line_stripped)
    if match:
        return line_stripped

    match = re.fullmatch(r"(Operator|Moderator|Host)", line_stripped, re.IGNORECASE)
    if match:
        return match.group(1).strip()

    name_colon_match = re.fullmatch(r"([A-Z][a-z'.]+(?:\s[A-Z][a-z'.]+){0,3}):", line_stripped)
    if name_colon_match:
        name_only = name_colon_match.group(1).strip()
        if participant_list_full:
            for p_full in participant_list_full:
                if p_full.lower().startswith(name_only.lower()):
                    if "--" in p_full or any(role.lower() in p_full.lower() for role in ["analyst", "officer", "director"]):
                        return p_full
        return name_only

    words = line_stripped.split()
    if 1 <= len(words) <= 4 and all(word[0].isupper() for word in words) and not re.search(r"[.!?,;]$", line_stripped):
        if line_stripped.lower() not in ["thank you", "good morning", "good afternoon", "good evening", "questions and answers", "prepared remarks"]:
            name_only = line_stripped
            if participant_list_full:
                for p_full in participant_list_full:
                    if p_full.lower().startswith(name_only.lower()):
                         if "--" in p_full or any(role.lower() in p_full.lower() for role in ["analyst", "officer", "director"]):
                            return p_full
            return name_only
    return None

def enrich_metadata_from_content(first_lines: list, current_metadata: dict) -> dict:
    """
    Tries to find year, quarter, company name from first_lines and adds/updates
    current_metadata if these fields are not already present or have placeholder values.
    """
    text_to_search = " ".join(first_lines)

    # Try to find year and quarter if not present or placeholder
    # Only update if current value is a placeholder like "YYYY" or "QX"
    if current_metadata.get("year", "YYYY") == "YYYY" or current_metadata.get("quarter", "QX") == "QX":
        year_quarter_match = re.search(r"(\d{4})\s+(First|Second|Third|Fourth)\s+Quarter", text_to_search, re.IGNORECASE)
        if year_quarter_match:
            if current_metadata.get("year", "YYYY") == "YYYY":
                current_metadata["year"] = year_quarter_match.group(1)
            
            if current_metadata.get("quarter", "QX") == "QX":
                quarter_str_from_text = year_quarter_match.group(2).lower()
                q_map = {"first": "Q1", "second": "Q2", "third": "Q3", "fourth": "Q4"}
                current_metadata["quarter"] = q_map.get(quarter_str_from_text, "QX")

    # Try to find company name if not present or seems generic
    if not current_metadata.get("company_name") or current_metadata.get("company_name", "").lower() == "company":
        company_patterns = [
            # Pattern for "Welcome to the [Company Name] [Year] [Quarter] Quarter ... Conference Call"
            r"welcome to the ([\w\s\.'&-]+?)(?:\s+\d{4}\s+(?:First|Second|Third|Fourth)\s+Quarter|\s+earnings conference call)",
            # Pattern for "Operator: Good day, and welcome to the [Company Name] Conference Call."
            r"Operator:\s*Good day, and welcome to the ([\w\s\.'&-]+?)\s+(?:Q\d\s\d{4}\s)?(?:Earnings )?Conference Call",
             # Pattern for "[Company Name] ([Ticker]) QX YYYY Earnings Call" often found in titles
            r"^([\w\s\.'&-]+?)\s+\([A-Z0-9:\.]+?\)\s+Q\d\s+\d{4}\s+Earnings\s+Call",
            # General patterns like "conference call for [Company Name]"
            r"(?:conference call for|earnings call of|results of)\s+([\w\s\.'&-]+?)(?:,|Company|Inc\.?|LLC\.?|$)"
        ]
        for pattern in company_patterns:
            company_match = re.search(pattern, text_to_search, re.IGNORECASE)
            if company_match:
                potential_name = company_match.group(1).strip()
                if potential_name and potential_name.lower() not in ["company", "the company"]:
                    current_metadata["company_name"] = potential_name
                    break 
    return current_metadata


def process_transcript_to_json_speaker_turns(
    transcript_content: str,
    output_filename: str,
    base_doc_metadata: dict
):
    processing_target_id = base_doc_metadata.get('conceptual_filename', base_doc_metadata.get('ticker', 'UNKNOWN'))
    logging.info(f"Processing transcript for {processing_target_id} -> {output_filename}")

    if not transcript_content or not transcript_content.strip():
        logging.warning(f"Empty transcript content for {processing_target_id}. Skipping.")
        return

    # --- Document Level Metadata & Initial Normalization ---
    doc_metadata = base_doc_metadata.copy()
    # Enrich with info from the raw transcript content itself if needed (use first ~30 lines of raw content)
    doc_metadata = enrich_metadata_from_content(transcript_content.splitlines()[:30], doc_metadata)

    full_content = normalize_text_generic(transcript_content)
    
    # --- Participant List Extraction ---
    participants_full_strings = []
    # Enhanced regex to find "Call Participants:", "Participants:", "Executives:", "Analysts:" etc.
    participants_section_match = re.search(
        r"(?:Call Participants|Participants|Conference Call Participants|Executives|Analysts|Speakers):\s*\n(.*?)(?:\n\n|\n[A-ZÀ-ÖØ-Þ][\w\s,&'\.-]+:|Prepared Remarks:|Questions and Answers:)",
        full_content, re.IGNORECASE | re.DOTALL
    )
    if participants_section_match:
        participants_section = participants_section_match.group(1)
        # Split by newline, also handle cases where participants are comma-separated on few lines
        raw_lines_or_comma_separated = []
        for line in participants_section.splitlines():
            if ',' in line and '--' not in line: # Heuristic: comma-separated list of names without titles
                 raw_lines_or_comma_separated.extend(p.strip() for p in line.split(','))
            else:
                 raw_lines_or_comma_separated.append(line.strip())

        for rpl in raw_lines_or_comma_separated:
            if not rpl: continue
            # Keep lines with "--" (name -- title) or typical name-only lines (1-4 words, likely capitalized)
            # or lines that are just names (e.g. from a comma separated list)
            is_short_capitalized_line = (len(rpl.split()) <= 5 and len(rpl) > 2 and not rpl.lower().startswith(("more ", "all ")))
            if "--" in rpl or is_short_capitalized_line:
                # Clean up potential artifacts like leading bullets or numbers
                cleaned_rpl = re.sub(r"^[*\-\d\.]+\s*", "", rpl).strip().rstrip(':')
                if cleaned_rpl:
                    participants_full_strings.append(cleaned_rpl)

        participants_full_strings = list(set(p for p in participants_full_strings if p and len(p.split()) < 10)) # Filter out long non-participant lines
        if participants_full_strings:
            doc_metadata["extracted_participants"] = participants_full_strings
            logging.debug(f"Extracted full participant strings for {processing_target_id}: {participants_full_strings}")
        else:
            logging.debug(f"No participant strings extracted for {processing_target_id} from section.")


    # --- Boilerplate Removal ---
    temp_text = full_content
    boilerplate_markers = [
        ("Please note the discussion today will contain forward-looking statements", "except as required by law."),
        ("During today's call, management will also discuss certain non-GAAP financial measures", "news release issued earlier today."),
        ("As a reminder, this conference call is being recorded.", "ir.[\\w\\.-]+com[\\.\\w\\/]*"), # More generic IR site
        (r"\[Operator Instructions\]", r"\[Operator Instructions\]"), # Often appears multiple times
        (r"Thank you, operator\.", r"Thank you, operator\."),
        (r"Your first question(?: in queue)? comes from the line of .*?\.\s*Your line is open\.", r"Your first question(?: in queue)? comes from the line of .*?\.\s*Your line is open\."),
        (r"Our next question comes from the line of .*?\.\s*Your line is now open\.", r"Our next question comes from the line of .*?\.\s*Your line is now open\."),
        (r"And that concludes the question-and-answer session\.", r"Have a great day\."),
        (r"Duration: \d+ minutes", r"All earnings call transcripts|Copyright © \d{4}|Thomson Reuters .*? transcript"), # End markers for duration
        (r"(?:Call Participants|Participants|Conference Call Participants|Executives|Analysts|Speakers):.*?(?=\n\n|\n[A-ZÀ-ÖØ-Þ][\w\s,&'\.-]+:|Prepared Remarks:|Questions and Answers:|$)", r"(?:Call Participants|Participants|Conference Call Participants|Executives|Analysts|Speakers):.*?(?=\n\n|\n[A-ZÀ-ÖØ-Þ][\w\s,&'\.-]+:|Prepared Remarks:|Questions and Answers:|$)") # More robust end for participants section
    ]

    for start_marker_regex, end_marker_regex in boilerplate_markers:
        try:
            start_re = re.compile(start_marker_regex, re.IGNORECASE | re.DOTALL)
            end_re = re.compile(end_marker_regex, re.IGNORECASE | re.DOTALL)
            
            # For patterns that might appear multiple times, remove all occurrences
            if start_marker_regex == end_marker_regex: # For self-contained markers like [Operator Instructions]
                temp_text = start_re.sub('', temp_text)
                continue

            new_text_parts = []
            last_end = 0
            for start_match in start_re.finditer(temp_text):
                start_idx = start_match.start()
                new_text_parts.append(temp_text[last_end:start_idx])
                
                # Search for end marker *after* the start marker
                end_match = end_re.search(temp_text, pos=start_match.end())
                if end_match:
                    last_end = end_match.end()
                else: # If end marker not found, make a conservative removal
                    # For specific critical sections like Duration or Participants, remove till end of doc if no clear end_marker
                    if start_marker_regex.startswith("Duration:") or "(?:Call Participants|Participants|Conference Call Participants|Executives|Analysts|Speakers):" in start_marker_regex :
                        logging.debug(f"Boilerplate section '{start_marker_regex}' started but no clear end found. Removing till end of document from match point.")
                        last_end = len(temp_text) # Remove till end of document
                    else:
                        # Otherwise, remove just the line/paragraph of the start_marker
                        line_end_m = re.search(r"(\n|$)", temp_text, pos=start_match.end())
                        last_end = line_end_m.start() if line_end_m else start_match.end()
                        logging.debug(f"Boilerplate section '{start_marker_regex}' started but no clear end found. Removing only the start line/paragraph.")
                # Break after first found section for some types of boilerplate to avoid over-removal if not careful
                # if start_marker_regex.startswith("Please note") or start_marker_regex.startswith("During today's call"):
                #    break 
            new_text_parts.append(temp_text[last_end:])
            temp_text = "".join(new_text_parts)
        except Exception as e: logging.debug(f"Boilerplate removal error for '{start_marker_regex}': {e}")
    
    lines = temp_text.splitlines()

    # --- Process into Speaker Turns ---
    speaker_turns = []
    current_speaker_full = "Unknown"
    current_section = "Introduction/Presentation" # Default section
    speech_accumulator = []
    turn_id_counter = 0

    def flush_speaker_turn():
        nonlocal speech_accumulator, current_speaker_full, current_section, speaker_turns, turn_id_counter
        if speech_accumulator:
            full_speech_block = "\n".join(speech_accumulator).strip()
            cleaned_block = clean_speech_text(full_speech_block)
            final_sentences = sentence_segment_and_filter(cleaned_block, min_sentence_words=2)
            if final_sentences:
                turn_id_counter += 1
                simple_name = current_speaker_full.split(' -- ')[0].strip()
                title = current_speaker_full.split(' -- ')[1].strip() if ' -- ' in current_speaker_full else "N/A"
                
                # If title is N/A but simple_name is generic (Operator, Moderator), reflect that
                if title == "N/A" and simple_name.lower() in ["operator", "moderator", "host"]:
                    title = simple_name # Use "Operator" as title if it was parsed as simple_name

                speaker_turns.append({
                    "turn_id": f"{doc_metadata.get('ticker','UNK')}_{doc_metadata.get('year','YYYY')}_{doc_metadata.get('quarter','QX')}_turn{turn_id_counter:03d}",
                    "speaker_full": current_speaker_full,
                    "speaker_simple_name": simple_name,
                    "speaker_title_affiliation": title,
                    "section": current_section,
                    "text": final_sentences
                })
            speech_accumulator = []

    for i, line_text in enumerate(lines):
        line_stripped = line_text.strip()
        if not line_stripped: continue

        # Section detection
        if line_stripped.lower().startswith("prepared remarks") or line_stripped.lower().startswith("presentation"):
            flush_speaker_turn()
            current_section = "Prepared Remarks"
            current_speaker_full = "Unknown" # Reset speaker at section change
            continue
        elif line_stripped.lower().startswith("questions and answers") or line_stripped.lower().startswith("q&a"):
            flush_speaker_turn()
            current_section = "Q&A"
            current_speaker_full = "Unknown" # Reset speaker at section change
            continue

        potential_new_speaker_full = is_potential_speaker_line_with_titles(line_stripped, participants_full_strings)
        
        if potential_new_speaker_full:
            # Basic lookahead: if the next non-empty line doesn't look like speech, it might be a multi-line title
            # This is a simplified heuristic. True speaker detection can be much more complex.
            is_true_speaker_line = True # Default assumption
            if i + 1 < len(lines):
                next_line_stripped = lines[i+1].strip()
                if not next_line_stripped or is_potential_speaker_line_with_titles(next_line_stripped, participants_full_strings) or \
                   next_line_stripped.lower().startswith(("prepared remarks", "questions and answers", "q&a")):
                    # If next line is empty, another speaker, or a section header, current line is likely a speaker.
                    pass
                elif len(next_line_stripped.split()) < 3 and next_line_stripped[0].islower():
                    # If next line is very short and starts lowercase, current line might be content.
                    # This is tricky and can misclassify.
                    # is_true_speaker_line = False # Commented out for now to be less aggressive
                    pass


            if is_true_speaker_line:
                flush_speaker_turn()
                current_speaker_full = potential_new_speaker_full
                # If the speaker line itself contains common intro phrases, don't add it to speech
                if re.match(r"^(Okay|Great|Alright|All right|Thank you|Thanks|Yes|Well|So|And now|Next question).{0,20}$", line_stripped, re.IGNORECASE): # Check if this line is just an intro
                    pass # Don't add this line as speech
                elif line_stripped.endswith(":") and line_stripped.lower() == potential_new_speaker_full.lower() + ":": # Speaker:
                    pass # Speaker identifier only, speech starts next line
                else: # Line contains speaker AND start of speech
                    speech_after_speaker = line_stripped[len(potential_new_speaker_full):].lstrip(": ")
                    if speech_after_speaker:
                         speech_accumulator.append(speech_after_speaker)
                continue
        
        speech_accumulator.append(line_text)

    flush_speaker_turn()

    if not speaker_turns:
        logging.warning(f"No speaker turns generated for {processing_target_id} after processing.")
        # Optionally, save an empty JSON or skip file creation
        # For now, we'll create a JSON with empty speaker_turns list if metadata exists
        # return # If you want to skip creating the file

    # --- Prepare Final JSON Output ---
    output_data = {
        "document_metadata": doc_metadata,
        "speaker_turns": speaker_turns
    }

    try:
        with open(output_filename, 'w', encoding='utf-8') as f:
            json.dump(output_data, f, ensure_ascii=False, indent=2)
        if speaker_turns: # Only log success if turns were actually generated
             logging.info(f"Successfully processed {processing_target_id} into JSON with {len(speaker_turns)} speaker turns -> {output_filename}")
        else:
             logging.info(f"Processed {processing_target_id}, but no speaker turns extracted. Output JSON saved: {output_filename}")
    except Exception as e:
        logging.error(f"Could not write JSON output file {output_filename}: {e}")



if __name__ == "__main__":

    # === Configuration: YOU MUST UPDATE THESE if different ===
    pickle_file_path = "earnings_transcripts/motley-fool-data.pkl" # Path to your pickle file
    output_dir = "processed_transcripts_json"                     # Directory for JSON outputs

    # --- Column names from your DataFrame structure ---
    transcript_col = 'transcript'
    ticker_col = 'ticker'
    date_col = 'date'
    quarter_info_col = 'q'      # Column like '2020-Q2'
    exchange_col = 'exchange' # Optional: if you want to include it in metadata


    # exchange_col = 'exchange' # Optional: if you want to include it in metadata
    # === End Configuration ===

    os.makedirs(output_dir, exist_ok=True)

    if not os.path.exists(pickle_file_path):
        logging.error(f"Pickle file not found: {pickle_file_path}")
        exit(1)

    try:
        df = pd.read_pickle(pickle_file_path)
        logging.info(f"Successfully loaded DataFrame from {pickle_file_path}. Shape: {df.shape}")
    except Exception as e:
        logging.error(f"Error loading pickle file {pickle_file_path}: {e}")
        exit(1)

    # Basic check if essential columns exist
    essential_cols_from_example = [transcript_col, ticker_col, date_col, quarter_info_col]
    missing_cols = [col for col in essential_cols_from_example if col not in df.columns]
    if missing_cols:
        logging.warning(f"DataFrame might be missing some columns suggested by your example: {missing_cols}. Available columns: {df.columns.tolist()}")
        # We'll proceed, but year/quarter extraction might rely more on the 'date' column or text parsing.


    processed_count = 0
    error_count = 0
    for index, row in df.iterrows():
        try:
            transcript_text = row.get(transcript_col) # Use .get for safety
            if not isinstance(transcript_text, str) or not transcript_text.strip():
                logging.warning(f"Skipping DataFrame row {index} (Ticker: {row.get(ticker_col, 'N/A')}) due to empty or invalid transcript content.")
                continue

            # --- Prepare base metadata from DataFrame row ---
            base_metadata = {"original_df_index": index}

            # Ticker
            ticker_val = row.get(ticker_col)
            base_metadata["ticker"] = str(ticker_val).upper() if pd.notna(ticker_val) else "UNKNOWN_TICKER"

            # Year and Quarter - Prioritize 'q' column
            base_metadata["year"] = "YYYY"
            base_metadata["quarter"] = "QX"
            
            q_val = row.get(quarter_info_col)
            if pd.notna(q_val) and isinstance(q_val, str):
                q_match = re.match(r"(\d{4})-(Q[1-4])", str(q_val))
                if q_match:
                    base_metadata["year"] = q_match.group(1)
                    base_metadata["quarter"] = q_match.group(2)
                else:
                    logging.debug(f"Row {index}: Column '{quarter_info_col}' ('{q_val}') not in YYYY-QX format. Will try '{date_col}'.")

            # Fallback to 'date' column if 'q' didn't provide year/quarter
            if base_metadata["year"] == "YYYY" or base_metadata["quarter"] == "QX":
                date_val = row.get(date_col)
                if pd.notna(date_val):
                    try:
                        # Attempt to parse various date formats, including the one with "ET"
                        dt_object = pd.to_datetime(date_val, errors='coerce')
                        if pd.notna(dt_object):
                            if base_metadata["year"] == "YYYY":
                                base_metadata["year"] = str(dt_object.year)
                            if base_metadata["quarter"] == "QX":
                                quarter_month = (dt_object.month - 1) // 3 + 1
                                base_metadata["quarter"] = f"Q{quarter_month}"
                            base_metadata["full_date_parsed_from_df"] = dt_object.strftime('%Y-%m-%d')
                        else:
                             logging.warning(f"Could not parse date for row {index} (Ticker: {base_metadata['ticker']}, Date value: '{date_val}') with pandas.to_datetime. Year/Quarter might be inaccurate.")
                    except Exception as e:
                        logging.warning(f"Error parsing date for row {index} (Ticker: {base_metadata['ticker']}, Date value: '{date_val}'): {e}. Year/Quarter might be inaccurate.")
            
            base_metadata["original_date_col_value"] = str(row.get(date_col, '')) # Store original date string for reference
            base_metadata["original_q_col_value"] = str(row.get(quarter_info_col, '')) # Store original q string for reference



            # Exchange (Optional)
            if exchange_col in df.columns and pd.notna(row.get(exchange_col)):
                base_metadata["exchange"] = str(row.get(exchange_col)).split(":")[0].strip().upper()  


            # --- Generate output filename ---
            fn_ticker = re.sub(r'[^\w\.-]', '', base_metadata["ticker"])
            fn_year = base_metadata.get("year", "YYYY")
            fn_quarter = base_metadata.get("quarter", "QX")
            #create the folder for the ticker
            ticker_dir = os.path.join(output_dir, fn_ticker)
            os.makedirs(ticker_dir, exist_ok=True) # Ensure ticker directory exists

            output_json_filename = os.path.join(
                ticker_dir,
                f"{fn_year}_{fn_quarter}.json"
            )
            
            # This is used for logging within process_transcript_to_json_speaker_turns
            base_metadata["conceptual_filename"] = os.path.basename(output_json_filename).replace(".json", "")


            logging.debug(f"Processing DataFrame row {index}: Ticker {base_metadata['ticker']}, Year {fn_year}, Quarter {fn_quarter}")
            process_transcript_to_json_speaker_turns(
                transcript_content=transcript_text,
                output_filename=output_json_filename,
                base_doc_metadata=base_metadata
            )
            processed_count +=1
        except Exception as e:
            error_count +=1
            logging.error(f"Critical error processing DataFrame row {index} (Ticker: {row.get(ticker_col, 'N/A')}): {e}", exc_info=True) # exc_info=True gives traceback

    logging.info(f"Finished processing. Total rows from DataFrame: {len(df)}. Successfully processed: {processed_count}. Errors: {error_count}.")

In [ ]:
#This worked !!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!
import re, json, ftfy, os
from pathlib import Path
from nltk.tokenize import sent_tokenize   # run `python -m nltk.downloader punkt` once
from dateutil import parser
import logging

# ---------- 1. header/footer patterns ----------
HEADER_FOOTER_PATTERNS = [
    re.compile(r'^\s*TABLE OF CONTENTS\s*$',                 re.I),
    re.compile(r'^\s*INDEX TO FINANCIAL STATEMENTS\s*$',     re.I),
    re.compile(r'^\s*F-\d+\s*$|^\s*\d+\s*$',                 re.I),          # “F-3” or bare page numbers
    re.compile(r'^\s*(10-K|10-Q)\b.*$',                      re.I),          # “10-K 1 …”
    re.compile(r'^\s*Item\s+\d+[A-Z]?\.?.*\s+\d+\s*$',       re.I),          # “Item 1. Business 1”
    re.compile(r'^\s*THE ORIGINAL BARK COMPANY.*$',          re.I),          # company-specific header
]

def strip_headers_footers(text: str) -> str:
    lines = []
    for ln in text.splitlines():
        if any(pat.match(ln) for pat in HEADER_FOOTER_PATTERNS):
            continue
        lines.append(ln)
    return "\n".join(lines)

# ---------- 2. sentence-level cleaner ----------
def clean_text(text: str) -> str:
    text = ftfy.fix_text(text.replace('�', "'").replace('’', "'"))

    # split camelCase but keep “U.S.”
    text = re.sub(r'(?<=[a-z])(?=[A-Z][a-z])', ' ', text)

    # collapse whitespace
    text = re.sub(r'[\n\r\t]+', ' ', text)
    text = re.sub(r'\s{2,}', ' ', text).strip()
    #added the item 1 strip!!!!!!!!!!!!!!!!!!!!!!!!!!!!!
    
    # sentence split (NLTK if available, regex otherwise)
    sents = sent_tokenize(text) if sent_tokenize else re.split(r'(?<=[.!?])\s+(?=[A-Z(])', text)

    dedup, seen = [], set()
    for s in sents:
        norm = re.sub(r'\s+', ' ', s).strip().lower()
        if norm and norm not in seen:
            dedup.append(s.strip())
            seen.add(norm)

    return ' '.join(dedup)

# ---------- 3. main one-file cleaner ----------
def process_file(path: Path, dest_root: Path):
    data = json.loads(path.read_text(encoding="utf-8"))
    chunks = data.get("text_chunks", [])
    if data.get("filing_type") == "10-K":
        chunks = chunks[1:]                     # drop SEC header chunk

    # -------- cross-chunk de-duplication -----------------------------------
    joined, seen = [], set()
    for ch in chunks:
        if not ch or "us-gaap" in ch.lower():
            continue
        norm = re.sub(r'\s+', ' ', ch).strip().lower()
        if norm in seen:
            continue
        seen.add(norm)
        joined.append(ch.strip())

    full_text = ' '.join(joined)

    # -------- hard-cut everything before “ITEM 1.” -------------------------
    # m = re.search(r'(?i)\bITEM\s+1\.\s', full_text)
    m = re.search(
        r'''(?is)                 # i = ignore-case, s = dot matches newline
            Item                  # literally “Item” (no word-boundary)
            \s*1                  # spaces (optional) then the digit 1
            \s*[\.\u2022]         # a dot or the bullet ● some filings use
            (?!\d)                # NOT followed by another digit (skips Item 10.)
        ''',
        full_text,
        re.VERBOSE
        )
    if m:
        full_text = full_text[m.start():]
    else:
        print(f"Warning: 'Item 1.' not found in {path.name}")

    full_text = strip_headers_footers(full_text)
    full_text = clean_text(full_text)

    # -------- drop tiny leftovers -----------------------------------------
    MIN_WORDS = 50
    if len(full_text.split()) < MIN_WORDS:
        logging.info("Dropped %s (only %d words)", path, len(full_text.split()))
        # print(f"Warning: {path.name} has too few words ({len(full_text.split())}). Skipping.")
        return                         # nothing written

    # =======================  METADATA BLOCK  ==============================
    date_str = data.get("date")                       # e.g. "2022-12-21"
    try:
        year_of_filing = parser.parse(date_str).year if date_str else None
    except Exception as e:
        print(f"Could not parse year from {date_str}: {e}")
        year_of_filing = None

    source_url   = data.get("url")                    # e.g. ".../data/1090872/..."
    cik_match    = re.search(r"/data/(\d+)/", source_url or "")
    extracted_cik = cik_match.group(1).zfill(10) if cik_match else None

    out = {
        "cleaned_text": full_text,
        "ticker":      data.get("ticker"),
        "date":        date_str,
        "year":        year_of_filing,
        "cik":         extracted_cik,
        "filing_type": data.get("filing_type"),
    }
    # ======================================================================

    # mirror raw-path subtree under sec_filings_clean/
    out_path = dest_root / path.relative_to(RAW_ROOT)
    out_path.parent.mkdir(parents=True, exist_ok=True)
    out_path.write_text(json.dumps(out, ensure_ascii=False, indent=2),
                        encoding="utf-8")

# ---------- 4. batch driver ----------
# -----------------------------------------
# 5.  ultra-simple batch driver (no Pool) 
# -----------------------------------------
if __name__ == "__main__":
    import glob, sys
    from tqdm import tqdm

    RAW_ROOT   = Path("sec_filings")
    CLEAN_ROOT = Path("sec_filings_clean")


    files = glob.glob(str(RAW_ROOT / "**/*.json"), recursive=True)
    if not files:
        sys.exit("No raw filings found under sec_filings/")

    errors = 0
    for fp in tqdm(files, desc="Cleaning filings"):
        try:
            process_file(Path(fp), CLEAN_ROOT)
            print(f"Cleaned: {fp}")
        except Exception as e:
            errors += 1
            with open("clean_errors.log", "a", encoding="utf-8") as log:
                log.write(f"{fp}\t{e}\n")

    print(f"\nDone.  {len(files)-errors} cleaned, {errors} errors (see clean_errors.log)")





In [ ]:

#only confifured for Apple filings, but can be adapted for others
import re
import json
import ftfy
import os
from pathlib import Path
from dateutil import parser
import logging

# Configure logging
logging.basicConfig(level=logging.INFO, format='%(asctime)s - %(levelname)s - %(message)s')

# ---------- 1. Apple-specific header/footer patterns ----------
HEADER_FOOTER_PATTERNS_APPLE = [
    re.compile(r'^\s*TABLE OF CONTENTS\s*$', re.IGNORECASE),
    re.compile(r'^\s*INDEX TO FINANCIAL STATEMENTS\s*$', re.IGNORECASE),
    re.compile(r'^\s*Apple Inc\.\s*\|\s*(Q\d\s+\d{4}|FY\d{4})?\s*Form (10-K|10-Q)\s*\|\s*\d+\s*$', re.IGNORECASE),
    re.compile(r'^\s*F-\d+\s*$|^\s*\d+\s*$', re.IGNORECASE),
    # Removed the general Item ToC line to avoid over-stripping within content
    # Add any other persistent Apple-specific headers/footers you observe
]

# Regex to find the start of significant content
# For 10-K: Look for the last "PART I...Item 1."
# For 10-Q: Look for the first "PART I...Item 1." or just "Item 1." if "PART I" is missing
START_PATTERN_10K_LAST = re.compile(
    r"""
    \bPART\s+I\s*[,]?\s*Item\s+1\s*[\.\u2022] # PART I, optional comma, Item 1, dot or bullet
    """,
    re.IGNORECASE | re.VERBOSE
)

START_PATTERN_10Q_FIRST = re.compile(
    r"""
    (?: \bPART\s+I\s*[,]?\s*)? Item\s+1\s*[\.\u2022] # Optional "PART I", then "Item 1."
    """,
    re.IGNORECASE | re.VERBOSE
)


def strip_specific_headers_footers(text: str) -> str:
    lines = []
    for ln in text.splitlines():
        if any(pat.match(ln) for pat in HEADER_FOOTER_PATTERNS_APPLE):
            continue
        lines.append(ln)
    return "\n".join(lines)

def clean_narrative_text_apple(text: str) -> str:
    if not text:
        return ""
    text = ftfy.fix_text(text.replace('�', "'").replace('’', "'"))
    text = re.sub(r'(?<=[a-z])(?=[A-Z][a-z])', ' ', text) # split camelCase
    text = re.sub(r'[\n\r\t]+', ' ', text) # collapse newlines etc. to spaces
    text = re.sub(r'\s{2,}', ' ', text).strip() # collapse multiple spaces
    return text


def find_last_match_start(pattern, text):
    last_match = None
    for match in pattern.finditer(text):
        last_match = match
    return last_match.start() if last_match else -1

def process_file_apple_v2(path: Path, dest_root: Path, raw_root: Path):
    try:
        data = json.loads(path.read_text(encoding="utf-8"))
    except json.JSONDecodeError as e:
        logging.error(f"Error decoding JSON from {path}: {e}")
        return
    except Exception as e:
        logging.error(f"Error reading file {path}: {e}")
        return

    chunks = data.get("text_chunks", [])
    filing_type = data.get("filing_type")
    ticker = data.get("ticker")

    if not chunks:
        logging.warning(f"No text_chunks found in {path.name}")
        return
    if not filing_type:
        logging.warning(f"No filing_type found in {path.name}, skipping.")
        return
    if ticker != "AAPL": # Ensure we only process Apple files if this script is specific
        logging.info(f"Skipping non-AAPL file: {path.name} (ticker: {ticker})")
        return


    # 1. Initial chunk filtering and joining (less aggressive here)
    # For 10-K, skip the very first chunk (SEC boilerplate often before ToC)
    start_index = 1 if filing_type == "10-K" else 0
    
    # Join all available chunks (after initial skip for 10-K)
    # We will do more targeted content cutting later
    full_doc_text_from_chunks = ' '.join(chunks[start_index:])
    if not full_doc_text_from_chunks.strip():
        logging.warning(f"No text after initial chunk joining for {path.name}")
        return

    # 2. Determine the actual start of content based on filing type
    content_start_index = -1
    if filing_type == "10-K":
        # Find the *last* occurrence of "PART I...Item 1."
        content_start_index = find_last_match_start(START_PATTERN_10K_LAST, full_doc_text_from_chunks)
        if content_start_index == -1: # Fallback if "PART I" isn't found
            logging.warning(f"10-K: 'PART I Item 1.' not found in {path.name}. Trying 'Item 1.'")
            match_item1 = START_PATTERN_10Q_FIRST.search(full_doc_text_from_chunks) # Use 10-Q logic for fallback
            if match_item1:
                content_start_index = match_item1.start()
    elif filing_type == "10-Q":
        # Find the *first* occurrence of "Item 1." (possibly with "PART I")
        match = START_PATTERN_10Q_FIRST.search(full_doc_text_from_chunks)
        if match:
            content_start_index = match.start()
    
    if content_start_index == -1:
        logging.warning(f"Could not find suitable start pattern for {path.name} ({filing_type}). Processing from beginning of joined chunks (after initial 10-K skip).")
        main_content_text = full_doc_text_from_chunks
    else:
        main_content_text = full_doc_text_from_chunks[content_start_index:]
        logging.info(f"Extracted content from index {content_start_index} for {path.name}")

    if not main_content_text.strip():
        logging.warning(f"No text after attempting to find start of content for {path.name}")
        return

    # 3. Apply cleaning to this larger block of text
    cleaned_text = ftfy.fix_text(main_content_text) # Fix encoding early on the whole block
    cleaned_text = strip_specific_headers_footers(cleaned_text)
    cleaned_text = clean_narrative_text_apple(cleaned_text) # This applies ftfy again, which is fine

    # -------- Word Count Check (adjust threshold as needed) -------------
    MIN_WORDS = 50 # Lowered because we are taking a larger block now
    word_count = len(cleaned_text.split())

    if word_count < MIN_WORDS:
        logging.warning(f"Dropped {path.name} ({filing_type}) as it has too few words ({word_count}) after cleaning. Original chunks had text.")
        return

    # =======================  METADATA BLOCK  ==============================
    date_str = data.get("date")
    try:
        year_of_filing = parser.parse(date_str).year if date_str else None
    except Exception as e:
        logging.warning(f"Could not parse year from {date_str} for {path.name}: {e}")
        year_of_filing = None

    source_url = data.get("url")
    cik_match = re.search(r"/data/(\d+)/", source_url or "")
    extracted_cik = cik_match.group(1).zfill(10) if cik_match else None

    output_data = {
        "cleaned_text": cleaned_text,
        "ticker": ticker, # Use ticker retrieved earlier
        "date": date_str,
        "year": year_of_filing,
        "cik": extracted_cik,
        "filing_type": filing_type,
        "source_filename": path.name,
    }
    # ======================================================================

    out_path = dest_root / path.relative_to(raw_root)
    out_path.parent.mkdir(parents=True, exist_ok=True)
    try:
        out_path.write_text(json.dumps(output_data, ensure_ascii=False, indent=2), encoding="utf-8")
        logging.info(f"Successfully processed and saved: {out_path.name} (words: {word_count})")
    except Exception as e:
        logging.error(f"Error writing output file {out_path}: {e}")

# --- Main Execution ---
if __name__ == "__main__":

    # MAKE SURE THESE PATHS ARE CORRECT FOR YOUR SETUP
    raw_path = "sec_filings/AAPL"
    dest_path = "sec_filings_clean/AAPL"
    RAW_ROOT = Path(raw_path)
    DEST_ROOT = Path(dest_path)

    if not RAW_ROOT.exists():
        logging.error(f"Raw data directory not found: {RAW_ROOT}")
        exit()
    
    DEST_ROOT.mkdir(parents=True, exist_ok=True)

    file_paths_to_process = list(RAW_ROOT.glob("**/*.json"))

    if not file_paths_to_process:
        logging.warning(f"No JSON files found in {RAW_ROOT}")

    for file_path in file_paths_to_process:
        if file_path.is_file():
            logging.info(f"Processing {file_path.name}...")
            print(f"Processing {file_path.name}...")
            process_file_apple_v2(file_path, DEST_ROOT, RAW_ROOT)
        else:
            logging.warning(f"Skipping non-file entry: {file_path}")

    logging.info("Processing complete.")

Processing 2025-01-30.json...
Processing 2024-10-24.json...


In [3]:
import gzip, csv, itertools, aiohttp, asyncio, re, json, os, textwrap

FORM_TYPES  = {"10-K", "10-Q"}

# Define DATA_ROOT, used in fetch_and_store
DATA_ROOT = "test" # Or your desired path

# --- CONFIG for CIK lookup ---
CIK_LOOKUP_URL = "https://www.sec.gov/files/company_tickers.json"
LOOKUP_HEADERS = {
    "User-Agent": "University_Project_Financial_LLM (muie.restante@gmail.com)",
    "Accept-Encoding": "gzip, deflate",
    "Host": "www.sec.gov"
}
DELAY_LOOKUP = 0.1 # Adjusted delay for a single request

async def download_ciks(session):
    """Downloads the CIK lookup file and extracts all CIK numbers."""
    try:
        print("Fetching CIK lookup data...")
        async with session.get(CIK_LOOKUP_URL, headers=LOOKUP_HEADERS) as resp:
            await asyncio.sleep(DELAY_LOOKUP) # Be respectful to SEC servers
            if resp.status != 200:
                print(f"Failed to fetch CIK lookup: Status {resp.status}")
                return []
            content_type = resp.headers.get("Content-Type", "")
            if "application/json" not in content_type:
                print(f"Unexpected content-type for CIK lookup: {content_type}")
                return []
            data = await resp.json()
            ciks = [str(entry["cik_str"]).zfill(10) for entry in data.values()]
            print(f"Successfully fetched {len(ciks)} CIKs.")
            return ciks
    except Exception as e:
        print(f"Error during CIK lookup download: {e}")
        return []

async def initialize_ciks():
    """Initializes the CIK list."""
    async with aiohttp.ClientSession() as session:
        return await download_ciks(session)

my_cik_list = [] # Will be populated by initialize_ciks
CIK_SET     = set(my_cik_list)              # 4–10 k entities
QUARTER_URL = "https://www.sec.gov/Archives/edgar/full-index/2025/Q2/master.gz" # Current date is May 16, 2025. Adjusted to Q2 2025.
UA = "MyResearchBot/1.0 (Muie; muie.restante@gmail.com) requests for academic research - contact for questions"

async def master_rows():
    if not CIK_SET:
        print("CIK_SET is empty. No data to fetch.")
        return
    headers = {
    "User-Agent": UA,
    "Accept": "*/*",
    "Referer": "https://www.sec.gov/",
    "Host": "www.sec.gov"
        }
    async with aiohttp.ClientSession(headers=headers) as s:
        async with s.get(QUARTER_URL, timeout=30) as r:
            if r.status != 200:
                print(f"Failed to fetch master file: Status {r.status}")
                return
            try:
                content = await r.read()
                decompressed_content = gzip.decompress(content).decode()
                rows = decompressed_content.splitlines()
                 # Find the header line index dynamically
                header_line_index = -1
                for i, line_content in enumerate(rows):
                    if line_content.startswith("CIK|Company Name|Form Type|Date Filed|File Name"):
                        header_line_index = i
                        break
                
                if header_line_index == -1:
                    print("Master file header not found. Cannot parse.")
                    return

                # Start processing from the line after the header
                relevant_rows = rows[header_line_index + 1:]

            except gzip.BadGzipFile:
                print(f"Error decompressing master file from {QUARTER_URL}. It might be corrupted or not gzipped.")
                # Attempt to read as plain text if decompression fails and it's small
                if len(content) < 1024 * 1024: # 1MB threshold
                    try:
                        plain_text_content = content.decode()
                        rows = plain_text_content.splitlines()
                        header_line_index = -1
                        for i, line_content in enumerate(rows):
                            if line_content.startswith("CIK|Company Name|Form Type|Date Filed|File Name"):
                                header_line_index = i
                                break
                        if header_line_index == -1:
                            print("Master file header not found in plain text attempt.")
                            return
                        relevant_rows = rows[header_line_index + 1:]
                        print("Successfully read master file as plain text after gzip error.")
                    except Exception as plain_text_err:
                        print(f"Could not read master file as plain text either: {plain_text_err}")
                        return
                else:
                    return # Don't process if large and ungzipped

    for row_data in csv.reader(relevant_rows, delimiter="|"):
        if len(row_data) < 5: # Ensure row has enough columns
            continue
        cik, _, form, date, path = row_data
        if form in FORM_TYPES and cik in CIK_SET:
            yield cik.zfill(10), form, date, f"https://www.sec.gov/Archives/{path}"

async def fetch_and_store(sema, row_info):
    cik, form, date, url = row_info
    # Ensure DATA_ROOT is defined and accessible
    if not DATA_ROOT:
        print("DATA_ROOT is not defined. Cannot save file.")
        return

    dir_path = os.path.join(DATA_ROOT, cik, form)
    fname = os.path.join(dir_path, f"{date}.txt")
    
    if os.path.exists(fname):                                 # incremental run
        # print(f"File {fname} already exists. Skipping.")
        return
    
    print(f"Fetching: {url}")
    try:
        async with sema, aiohttp.ClientSession(headers={"User-Agent": UA}) as s:
            await asyncio.sleep(DELAY_LOOKUP) # Respect SEC rate limits
            async with s.get(url, timeout=60) as r: # Increased timeout for potentially large files
                if r.status == 200:
                    txt = (await r.read()).decode("utf-8", "ignore")
                    os.makedirs(dir_path, exist_ok=True)
                    with open(fname, "w", encoding="utf-8") as f:
                        f.write(txt)
                    print(f"Stored: {fname}")
                elif r.status == 404:
                    print(f"File not found (404): {url}")
                elif r.status == 403:
                    print(f"Access forbidden (403) for {url}. Check User-Agent or IP restrictions.")
                else:
                    print(f"Failed to fetch {url}: Status {r.status}")
    except asyncio.TimeoutError:
        print(f"Timeout fetching {url}")
    except Exception as e:
        print(f"Error fetching or storing {url}: {e}")


async def main():
    global my_cik_list, CIK_SET
    # Initialize CIKs first
    fetched_ciks = await initialize_ciks()
    if not fetched_ciks:
        print("No CIKs were fetched. Exiting.")
        return
    
    my_cik_list = fetched_ciks
    CIK_SET = set(my_cik_list)
    print(f"Working with {len(CIK_SET)} unique CIKs.")

    # Limit the number of CIKs for testing if needed
    CIK_SET = set(list(CIK_SET)[:1]) # Example: use only the first 10 CIKs
    print(f"DEBUG: Using a subset of {len(CIK_SET)} CIKs for processing.")


    if not CIK_SET:
        print("CIK list is empty after initialization. Cannot proceed.")
        return

    sema = asyncio.Semaphore(10) # Adjusted semaphore based on SEC's 10 req/s limit
    
    tasks = []
    async for row_details in master_rows():
        if row_details: # Ensure row_details is not None
            tasks.append(fetch_and_store(sema, row_details))
    
    if tasks:
        print(f"Gathered {len(tasks)} tasks to process.")
        await asyncio.gather(*tasks)
        print("All tasks completed.")
    else:
        print("No tasks to process based on the master file and CIK list.")

if __name__ == '__main__': # Required for Colab/Jupyter if running asyncio directly
    import nest_asyncio
    nest_asyncio.apply()
    asyncio.run(main())

Fetching CIK lookup data...
Successfully fetched 10039 CIKs.
Working with 7880 unique CIKs.
DEBUG: Using a subset of 1 CIKs for processing.
Failed to fetch master file: Status 403
No tasks to process based on the master file and CIK list.


In [3]:
import os
# Set the cache directory to a folder on your D: drive
# Make sure this path exists or can be created.
os.environ['HF_DATASETS_CACHE'] = 'D:\\huggingface_cache\\datasets' # Example path on D:

from datasets import load_dataset, DatasetDict
# Load the dataset for the 'train' split
# The original command includes DatasetDict in its import, so we keep it.
edgar_dataset_train = load_dataset('eloukas/edgar-corpus', split='train', trust_remote_code=True)
# Save it to a CSV file
edgar_dataset_train.to_csv('edgar_corpus_10k.csv')

# You can optionally print the cache directory to confirm
from datasets.config import HF_DATASETS_CACHE
print(f"Datasets cache directory is: {HF_DATASETS_CACHE}")

Creating CSV from Arrow format: 100%|██████████| 177/177 [09:01<00:00,  3.06s/ba]

Datasets cache directory is: C:\Users\Serban\.cache\huggingface\datasets


In [ ]:
import pandas as pd

chunksize = 10  # rows per chunk, tune based on your system
for chunk in pd.read_csv("edgar_corpus_10k.csv", chunksize=chunksize):
    # Process each chunk
    print(chunk.head())  # Example: preview first few rows of each chunk


In [3]:
import pandas as pd

# Step 1: Find column names without loading the whole file
df_sample = pd.read_csv("edgar_corpus_10k.csv", nrows=5)
print(df_sample.columns)  # See what you're working with


Index(['filename', 'cik', 'year', 'section_1', 'section_1A', 'section_1B',
       'section_2', 'section_3', 'section_4', 'section_5', 'section_6',
       'section_7', 'section_7A', 'section_8', 'section_9', 'section_9A',
       'section_9B', 'section_10', 'section_11', 'section_12', 'section_13',
       'section_14', 'section_15'],
      dtype='object')


In [5]:
import pandas as pd

# Define output file and sections of interest
output_file = "sample_filings.txt"
usecols = ['filename', 'cik', 'year', 'section_1', 'section_1A', 'section_1B',
       'section_2', 'section_3', 'section_4', 'section_5', 'section_6',
       'section_7', 'section_7A', 'section_8', 'section_9', 'section_9A',
       'section_9B', 'section_10', 'section_11', 'section_12', 'section_13',
       'section_14', 'section_15']
chunksize = 1
num_samples = 5  # how many filings you want to store

with open(output_file, "w", encoding="utf-8") as out:
    for i, chunk in enumerate(pd.read_csv("filtered_filings.csv", usecols=usecols, chunksize=chunksize)):
        row = chunk.iloc[0]
        out.write(f"\n\n=== Filing {i + 1} ===\n")
        out.write(f"Filename: {row['filename']}\n")
        out.write(f"CIK: {row['cik']}\n")
        out.write(f"Year: {row['year']}\n")

        for sec in ['section_1', 'section_1A', 'section_1B',
       'section_2', 'section_3', 'section_4', 'section_5', 'section_6',
       'section_7', 'section_7A', 'section_8', 'section_9', 'section_9A',
       'section_9B', 'section_10', 'section_11', 'section_12', 'section_13',
       'section_14', 'section_15']:
            out.write(f"\n--- {sec} ---\n")
            section_text = str(row[sec])
            # You can write full text or limit it:
            out.write(section_text)  # adjust char limit as needed
        out.write("\n" + "=" * 20 + "\n")

        if i + 1 == num_samples:
            break

print(f"Saved {num_samples} filings to {output_file}")


Saved 5 filings to sample_filings.txt


In [3]:
input_file = "edgar_corpus_10k.csv"
cutoff_year = 2017  
output_file = "filtered_filings.csv"

import pandas as pd

# Process the file in chunks to avoid MemoryError
chunk_size = 10000  # Adjust chunk size based on your available memory
first_chunk = True

# Open the output file in write mode for the first chunk, then append for subsequent chunks
with open(output_file, "w", encoding="utf-8") as f_out:
    for chunk in pd.read_csv(input_file, chunksize=chunk_size, encoding="utf-8"):
        # cut off the years before 2017
        filtered_chunk = chunk[chunk['year'] >= cutoff_year]
        # save the filtered chunk to the output file
        if not filtered_chunk.empty:
            if first_chunk:
                filtered_chunk.to_csv(f_out, index=False, encoding="utf-8", header=True)
                first_chunk = False
            else:
                filtered_chunk.to_csv(f_out, index=False, encoding="utf-8", header=False)

print(f"Filtered data saved to {output_file}")

Filtered data saved to filtered_filings.csv


In [11]:
import pandas as pd
import requests
import json
import os
from pathlib import Path

# --- CIK to Ticker Mapping Functions (keep as is from previous response) ---
_cik_to_ticker_map = None

def load_cik_ticker_mapping(force_reload=False):
    global _cik_to_ticker_map
    if _cik_to_ticker_map is not None and not force_reload:
        return _cik_to_ticker_map
    url = "https://www.sec.gov/files/company_tickers.json"
    headers = {"User-Agent": "Your Name/Org (your.email@example.com)"} # UPDATE THIS
    print("Fetching CIK to Ticker mapping from SEC...")
    try:
        response = requests.get(url, headers=headers)
        response.raise_for_status()
        data = response.json()
        _cik_to_ticker_map = {
            str(entry['cik_str']).zfill(10): entry['ticker']
            for entry in data.values()
        }
        print(f"CIK to Ticker mapping loaded successfully. {len(_cik_to_ticker_map)} entries.")
        return _cik_to_ticker_map
    except requests.exceptions.RequestException as e:
        print(f"Failed to fetch CIK-Ticker mapping: {e}")
        _cik_to_ticker_map = {}
        return _cik_to_ticker_map
    except json.JSONDecodeError as e:
        print(f"Failed to parse JSON from CIK-Ticker mapping: {e}")
        _cik_to_ticker_map = {}
        return _cik_to_ticker_map
    except KeyError as e:
        print(f"Unexpected JSON structure from SEC CIK-Ticker mapping. Missing key: {e}")
        _cik_to_ticker_map = {}
        return _cik_to_ticker_map

def get_ticker_from_cik(cik_str_padded, mapping):
    return mapping.get(cik_str_padded)

# --- Main Processing Logic ---

def process_csv_to_multiple_json_formats(
    csv_file_path="filtered_filings.csv",
    output_base_dir_rag="sec_filings_17_20_sectioned",
    output_base_dir_continuous="sec_filings_17_20_continuous",
    csv_chunksize=500,
    num_filings_to_process=None
):
    cik_ticker_map = load_cik_ticker_mapping()
    if not cik_ticker_map:
        print("Warning: CIK-Ticker mapping is empty. Tickers will not be resolved.")

    # Setup for RAG (sectioned) output
    output_base_path_rag = Path(output_base_dir_rag)
    output_base_path_rag.mkdir(parents=True, exist_ok=True)
    print(f"Output base path for RAG format: {output_base_path_rag}")
    unknown_tickers_path_rag = output_base_path_rag / "UNKNOWN_TICKERS"
    unknown_tickers_path_rag.mkdir(parents=True, exist_ok=True)
    print(f"Output path for unknown tickers in RAG format: {unknown_tickers_path_rag}")

    # Setup for Continuous Text output
    output_base_path_continuous = Path(output_base_dir_continuous)
    output_base_path_continuous.mkdir(parents=True, exist_ok=True)
    print(f"Output base path for Continuous Text format: {output_base_path_continuous}")
    unknown_tickers_path_continuous = output_base_path_continuous / "UNKNOWN_TICKERS"
    unknown_tickers_path_continuous.mkdir(parents=True, exist_ok=True)
    print(f"Output path for unknown tickers in Continuous Text format: {unknown_tickers_path_continuous}")


    section_cols_from_csv = ['section_1', 'section_1A', 'section_1B',
                             'section_2', 'section_3', 'section_4', 'section_5', 'section_6',
                             'section_7', 'section_7A', 'section_8', 'section_9', 'section_9A',
                             'section_9B', 'section_10', 'section_11', 'section_12', 'section_13',
                             'section_14', 'section_15']
    metadata_cols_from_csv = ['filename', 'cik', 'year']
    all_cols_to_read = metadata_cols_from_csv + section_cols_from_csv
    
    processed_count = 0

    print(f"Starting multi-format processing of {csv_file_path}...")
    try:
        for i, chunk_df in enumerate(pd.read_csv(csv_file_path, usecols=all_cols_to_read, chunksize=csv_chunksize, low_memory=False)):
            print(f"Processing CSV chunk {i+1}...")
            for index, row in chunk_df.iterrows():
                if num_filings_to_process is not None and processed_count >= num_filings_to_process:
                    print(f"Reached processing limit of {num_filings_to_process} filings.")
                    return

                # --- Extract and Validate Metadata (same for both formats) ---
                try:
                    filename = str(row['filename'])
                    cik_val = row['cik']
                    if pd.isna(cik_val):
                        print(f"Skipping row {index} in chunk {i+1}: CIK is missing.")
                        continue
                    try:
                        cik_int = int(float(cik_val))
                    except ValueError:
                        print(f"Skipping row {index} in chunk {i+1}: CIK '{cik_val}' is not valid.")
                        continue
                    cik_str_unpadded = str(cik_int)
                    
                    year_val = row['year']
                    if pd.isna(year_val):
                        print(f"Skipping row {index} in chunk {i+1}: Year is missing for CIK {cik_str_unpadded}.")
                        continue
                    try:
                        year_str = str(int(float(year_val)))
                    except ValueError:
                        print(f"Skipping row {index} in chunk {i+1}: Year '{year_val}' is not valid for CIK {cik_str_unpadded}.")
                        continue
                except KeyError as e:
                    print(f"Skipping row {index} in chunk {i+1}: Missing essential metadata column: {e}")
                    continue
                
                cik_padded = cik_str_unpadded.zfill(10)
                ticker = get_ticker_from_cik(cik_padded, cik_ticker_map)

                # --- Prepare Document-Level Metadata (same for both) ---
                doc_metadata = {
                    "filename": filename,
                    "cik": cik_str_unpadded,
                    "year": year_str,
                    "ticker": ticker if ticker else None
                }

                # --- 1. Prepare RAG-friendly (sectioned) JSON data ---
                rag_chunks_list = []
                section_texts_for_continuous = [] # For building the continuous text version

                for sec_col_name in section_cols_from_csv:
                    section_content = row.get(sec_col_name)
                    text_content = str(section_content) if pd.notna(section_content) else ""
                    
                    if text_content: # Only process/include sections with content
                        # For RAG format
                        first_line = text_content.split('\n', 1)[0].strip()
                        section_title = first_line if len(first_line) < 100 and "Item" in first_line else sec_col_name
                        rag_chunks_list.append({
                            "id": sec_col_name,
                            "title": section_title,
                            "text": text_content
                        })
                        # For continuous text format (add section header for clarity if desired)
                        section_texts_for_continuous.append(f"{text_content}")


                rag_output_data = {
                    "metadata": doc_metadata,
                    "chunks": rag_chunks_list
                }

                # --- 2. Prepare Continuous Text JSON data ---
                full_continuous_text = "".join(section_texts_for_continuous).strip()
                continuous_output_data = {
                    "metadata": doc_metadata, # Use the same metadata
                    "cleaned_text": full_continuous_text # Or just "text" if that matches newer files
                }

                # --- Determine output paths ---
                if not ticker:
                    company_dir_name_segment = f"CIK_{cik_padded}"
                    rag_parent_dir = unknown_tickers_path_rag
                    continuous_parent_dir = unknown_tickers_path_continuous
                else:
                    company_dir_name_segment = ticker.upper()
                    rag_parent_dir = output_base_path_rag
                    continuous_parent_dir = output_base_path_continuous
                
                # --- Save RAG-formatted JSON ---
                if rag_chunks_list: # Only save if there's content
                    rag_company_dir = rag_parent_dir / company_dir_name_segment
                    rag_company_dir.mkdir(parents=True, exist_ok=True)
                    rag_json_file_path = rag_company_dir / f"{year_str}.json"
                    try:
                        with open(rag_json_file_path, 'w', encoding='utf-8') as jf:
                            json.dump(rag_output_data, jf, indent=4)
                    except Exception as e:
                        print(f"Error writing RAG JSON {rag_json_file_path}: {e}")
                
                # --- Save Continuous Text JSON ---
                if full_continuous_text: # Only save if there's content
                    continuous_company_dir = continuous_parent_dir / company_dir_name_segment
                    continuous_company_dir.mkdir(parents=True, exist_ok=True)
                    continuous_json_file_path = continuous_company_dir / f"{year_str}.json"
                    try:
                        with open(continuous_json_file_path, 'w', encoding='utf-8') as jf:
                            json.dump(continuous_output_data, jf, indent=4)
                    except Exception as e:
                        print(f"Error writing Continuous Text JSON {continuous_json_file_path}: {e}")

                processed_count += 1
                if processed_count % (csv_chunksize // 10 if csv_chunksize > 10 else 1) == 0:
                    print(f"Processed {processed_count} filings (both formats). Last CIK: {cik_str_unpadded}, Year: {year_str}")
            
            if num_filings_to_process is not None and processed_count >= num_filings_to_process:
                break 
                
        print(f"\nFinished multi-format processing. Total filings processed: {processed_count}")

    except FileNotFoundError:
        print(f"Error: The CSV file '{csv_file_path}' was not found.")
    # ... (rest of CSV error handling) ...
    except pd.errors.EmptyDataError:
        print(f"Error: The CSV file '{csv_file_path}' is empty or all columns in usecols are missing.")
    except ValueError as e:
        print(f"Error reading CSV '{csv_file_path}': {e}. Check 'usecols' parameter.")
    except Exception as e:
        print(f"An unexpected error occurred during CSV processing: {e}")


if __name__ == '__main__':

    process_csv_to_multiple_json_formats(
        csv_file_path="filtered_filings.csv",
        output_base_dir_rag="sec_filings_17_20_sectioned",
        output_base_dir_continuous="sec_filings_17_20_continuous",
        csv_chunksize=1, 
        num_filings_to_process=None
    )

Fetching CIK to Ticker mapping from SEC...
CIK to Ticker mapping loaded successfully. 7881 entries.
Output base path for RAG format: sec_filings_17_20_sectioned
Output path for unknown tickers in RAG format: sec_filings_17_20_sectioned\UNKNOWN_TICKERS
Output base path for Continuous Text format: sec_filings_17_20_continuous
Output path for unknown tickers in Continuous Text format: sec_filings_17_20_continuous\UNKNOWN_TICKERS
Starting multi-format processing of filtered_filings.csv...
Processing CSV chunk 1...
Processed 1 filings (both formats). Last CIK: 1595248, Year: 2017
Processing CSV chunk 2...
Processed 2 filings (both formats). Last CIK: 1265131, Year: 2017
Processing CSV chunk 3...
Processed 3 filings (both formats). Last CIK: 1334933, Year: 2017
Processing CSV chunk 4...
Processed 4 filings (both formats). Last CIK: 1054721, Year: 2017
Processing CSV chunk 5...
Processed 5 filings (both formats). Last CIK: 1653558, Year: 2017
Processing CSV chunk 6...
Processed 6 filings (bot

In [15]:
import re
import json
import ftfy
import os
from pathlib import Path
import nltk # NLTK for sentence tokenization
from nltk.tokenize import sent_tokenize
import logging

# Ensure 'punkt' tokenizer models are downloaded for nltk
try:
    nltk.data.find('tokenizers/punkt')
except nltk.downloader.DownloadError:
    print("NLTK 'punkt' model not found. Downloading...")
    nltk.download('punkt')
except Exception as e: # Handle other potential exceptions during find
    print(f"Error checking for NLTK 'punkt' model: {e}. Attempting to download anyway.")
    nltk.download('punkt')


# Configure logging
logging.basicConfig(level=logging.INFO, format='%(levelname)s: %(message)s')

# ---------- 1. Text Cleaning Functions ----------

def normalize_text(text: str) -> str:
    """Fixes common encoding/Unicode issues and normalizes special characters."""
    # Fix encoding issues, weird characters like mojibake
    text = ftfy.fix_text(text)

    # Normalize various unicode characters to their simpler ASCII counterparts
    replacements = {
        '\u201c': '"', '\u201d': '"',  # Left/right double quotes
        '\u2018': "'", '\u2019': "'",  # Left/right single quotes
        '\u2022': '* ',               # Bullet point
        '\u2013': '-', '\u2014': '--', # En/Em dash
        '\u00A0': ' ',                # Non-breaking space
        # Add more replacements as needed
    }
    for unicode_char, replacement in replacements.items():
        text = text.replace(unicode_char, replacement)

    # Replace specific problematic characters not caught by ftfy or above
    text = text.replace('�', "'") # Replacement character

    return text

def clean_sec_text(text: str) -> str:
    """Applies SEC-specific and general text cleaning patterns."""
    # 1. Normalize line breaks and tabs to single spaces
    # This helps before sentence tokenization.
    text = re.sub(r'[\r\n\t]+', ' ', text)

    # 2. Remove or normalize redundant SEC item markers
    # e.g., "Item 1A.Item 1A. Risk Factors" -> "Item 1A. Risk Factors"
    # This pattern looks for "Item" followed by a number/letter combo and a dot,
    # then checks if it's immediately repeated.
    text = re.sub(r'(Item\s+\d+[A-Z]?\.(?:\s*\([a-z]\))?)(?:\s*\1)+', r'\1', text, flags=re.IGNORECASE)
    
    # 3. Split camelCase words but try to keep "U.S." and similar intact.
    # This is a common regex; it looks for a lowercase letter followed by an
    # uppercase letter that is itself followed by a lowercase letter (to avoid splitting acronyms).
    text = re.sub(r'(?<=[a-z])(?=[A-Z][a-z])', ' ', text)

    # 4. Collapse multiple spaces into a single space and strip leading/trailing whitespace
    text = re.sub(r'\s{2,}', ' ', text).strip()

    return text

def sentence_segment_and_deduplicate(text: str, min_sentence_words: int = 3) -> str:
    """Segments text into sentences, removes duplicates, and filters short sentences."""
    if not text:
        return ""

    try:
        sents = sent_tokenize(text)
    except Exception as e:
        logging.error(f"Sentence tokenization failed: {e}. Falling back to simple split.")
        # Fallback: split by common punctuation if sent_tokenize fails
        sents = re.split(r'(?<=[.!?])\s+(?=[A-Z0-9(])', text)
        if not sents: # if split results in empty or single non-sentence item
             sents = [text]


    deduplicated_sentences = []
    seen_sentences = set()

    for s in sents:
        # Normalize sentence for robust duplicate checking (lowercase, collapse whitespace)
        norm_s = re.sub(r'\s+', ' ', s).strip().lower()

        if norm_s and len(norm_s.split()) >= min_sentence_words and norm_s not in seen_sentences:
            deduplicated_sentences.append(s.strip()) # Keep original casing for the final text
            seen_sentences.add(norm_s)

    return ' '.join(deduplicated_sentences)


# ---------- 2. Main Processing Function ----------

def process_json_file(input_filepath: Path, output_filepath: Path):
    """Loads, cleans, and saves the text from a JSON file."""
    try:
        with open(input_filepath, 'r', encoding='utf-8') as f:
            data = json.load(f)
    except FileNotFoundError:
        logging.error(f"Input file not found: {input_filepath}")
        return
    except json.JSONDecodeError:
        logging.error(f"Error decoding JSON from file: {input_filepath}")
        return
    except Exception as e:
        logging.error(f"Could not read file {input_filepath}: {e}")
        return


    raw_text = data.get("cleaned_text")
    metadata = data.get("metadata", {}) # Ensure metadata is a dict

    if not raw_text:
        logging.warning(f"No 'cleaned_text' found in {input_filepath}. Skipping.")
        return

    # --- Cleaning Pipeline ---
    # Stage 1: Basic Unicode normalization
    text = normalize_text(raw_text)
    # logging.debug(f"After normalize_text:\n{text[:500]}\n")

    # Stage 2: SEC-specific and general structural cleaning
    text = clean_sec_text(text)
    # logging.debug(f"After clean_sec_text:\n{text[:500]}\n")

    # Stage 3: Sentence segmentation and deduplication
    cleaned_final_text = sentence_segment_and_deduplicate(text)
    # logging.debug(f"After sentence_segment_and_deduplicate:\n{cleaned_final_text[:500]}\n")

    MIN_WORDS_FOR_DOCUMENT = 50
    if len(cleaned_final_text.split()) < MIN_WORDS_FOR_DOCUMENT:
        logging.info(f"Document {input_filepath.name} has too few words ({len(cleaned_final_text.split())}) after cleaning. Skipping output.")
        return

    # Prepare output data
    output_data = {
        "metadata": metadata, # Use the original metadata
        "cleaned_text": cleaned_final_text
    }

    # Ensure output directory exists
    output_filepath.parent.mkdir(parents=True, exist_ok=True)

    try:
        with open(output_filepath, 'w', encoding='utf-8') as f:
            json.dump(output_data, f, ensure_ascii=False, indent=4)
        logging.info(f"Successfully processed and saved: {output_filepath}")
    except Exception as e:
        logging.error(f"Could not write output file {output_filepath}: {e}")


# ---------- 3. Example Usage ----------
if __name__ == "__main__":
    # Create a dummy input file for testing
   
    input_dir = "sec_filings_17_20_continuous"
    

    input_dir = Path(input_dir)
    input_dir.mkdir(exist_ok=True, parents=True)  # Ensure the input directory exists

    test_input_file = input_dir / "2018.json"


    # --- Process the file ---
    # If you have a folder of such files:
    for input_file_path in input_dir.glob("**/*.json"):
        #clean and replace the file with the xact same name
        output_file_path =  input_file_path
        process_json_file(input_file_path, output_file_path)

    # For a single file:
    # input_file_path = test_input_file # Use the one we just created
    # output_file_path = output_dir / "2018_cleaned.json"
    # process_json_file(input_file_path, output_file_path)


INFO: Successfully processed and saved: sec_filings_17_20_continuous\A\2018.json
INFO: Successfully processed and saved: sec_filings_17_20_continuous\A\2019.json
INFO: Successfully processed and saved: sec_filings_17_20_continuous\A\2020.json
INFO: Successfully processed and saved: sec_filings_17_20_continuous\AA\2017.json
INFO: Successfully processed and saved: sec_filings_17_20_continuous\AA\2018.json
INFO: Successfully processed and saved: sec_filings_17_20_continuous\AA\2019.json
INFO: Successfully processed and saved: sec_filings_17_20_continuous\AAAU\2018.json
INFO: Successfully processed and saved: sec_filings_17_20_continuous\AAAU\2019.json
INFO: Successfully processed and saved: sec_filings_17_20_continuous\AAAU\2020.json
INFO: Successfully processed and saved: sec_filings_17_20_continuous\AAGH\2017.json
INFO: Successfully processed and saved: sec_filings_17_20_continuous\AAGH\2018.json
INFO: Successfully processed and saved: sec_filings_17_20_continuous\AAGH\2019.json
INFO: S

In [21]:
import re
#these can only be used for the sec_filings_17_20_continuous files !!!!!!!

HEADER_RE = re.compile(
    r"\b"                       # word boundary
    r"(?:PART\s(?:I{1,3}|IV)\s+)?"  # optional “PART I–IV ”
    r"Item\s"                   
    r"(?P<num>(?:[1-9]|1[0-6])[A-Z]?)"  # 1–16 plus optional letter (captured)
    r"\."                       # literal dot
)

def split_sections2(text: str) -> list[str]:
    """Return a list where each element starts with its own header."""
    matches = list(HEADER_RE.finditer(text))
    if not matches:
        return [text.strip()] if text.strip() else []

    sections = []

    # introduction (anything before the first valid item)
    intro = text[:matches[0].start()].strip()
    if intro:
        sections.append(intro)

    # item-based slices
    for i, m in enumerate(matches):
        start = m.start()
        end   = matches[i + 1].start() if i + 1 < len(matches) else len(text)
        sections.append(text[start:end].strip())

    return sections

def process_sections2(sections: list[str], *, as_mapping: bool = False):
    """
    Convert each section to either
      • a dict {'item': <label>, 'text': <body>}, returned in a list (default), or
      • a mapping {<label>: <body>} if as_mapping=True.
    """
    section_names_dict = {
        "1": "Business",
        "1A": "Risk Factors",
        "1B": "Unresolved Staff Comments",
        "2": "Properties",
        "3": "Legal Proceedings",
        "4": "Mine Safety Disclosures",
        "5": "Market for Registrant’s Common Equity, Related Stockholder Matters and Issuer Purchases of Equity Securities",
        "6": "[Reserved]",
        "7": "Management’s Discussion and Analysis of Financial Condition and Results of Operations (MD&A)",
        "7A": "Quantitative and Qualitative Disclosures About Market Risk",
        "8": "Financial Statements and Supplementary Data",
        "9": "Changes in and Disagreements with Accountants on Accounting and Financial Disclosure",
        "9A": "Controls and Procedures",
        "9B": "Other Information",
        "9C": "Disclosure Regarding Foreign Jurisdictions that Prevent Inspections",
        "10": "Directors, Executive Officers and Corporate Governance",
        "11": "Executive Compensation",
        "12": "Security Ownership of Certain Beneficial Owners and Management and Related Stockholder Matters",
        "13": "Certain Relationships and Related Transactions, and Director Independence",
        "14": "Principal Accountant Fees and Services",
        "15": "Exhibits, Financial Statement Schedules",
        "16": "Form 10-K Summary (Optional)"
    }

        

        
    processed_list = []
    processed_map  = {}

    for sec in sections:
        # Does the section begin with a valid header?
        header_match = HEADER_RE.match(sec)
        if header_match:
            label = header_match.group("num")          # e.g. "1", "1A", "15B"
            section_name = section_names_dict.get(label, f"Item {label}")  

            body  = sec[header_match.end():].lstrip()  # remainder, no leading whitespace
        else:
            # Treat as “preface” or “misc”; you could skip or store under a special key
            label = "PREFACE"
            section_name = "Preface or Miscellaneous"
            body  = sec

        if as_mapping:
            processed_map[label] = body

        else:
            if len(body) > 500:
                processed_list.append({
                    "item": label,
                    "section": section_name,  
                    "text": body
                })


    return processed_map if as_mapping else processed_list


In [14]:
def cut_text_10K(text: str):
    """
    Cuts the text to keep everything from the last occurrence of "Item 1." onwards.
    The search is case-sensitive and includes the period.
    """
    search_string = "Item 1."
    last_occurrence_index = text.rfind(search_string)

    if last_occurrence_index != -1:
        return text[last_occurrence_index:]
    else:
        print("Warning: 'Item 1.' not found in the text. Returning the original text.")
        return text


In [26]:
#clean and partition the files
from pathlib import Path
directory = "sec_filings_clean"
directory = Path(directory)
output_directory = "10-K_sectioned_newer"
output_directory = Path(output_directory)

output_directory.mkdir(exist_ok=True, parents=True)  # Ensure the output directory exists

for file_path in directory.glob("**/10-K/*.json"):
    try:
        with open(file_path, 'r', encoding='utf-8') as f:
            data = json.load(f)
            if data.get("metadata") is None:
                ticker  = data.get("ticker")
                date = data.get("date",None)
                cik = data.get("cik")
                year = data.get("year", "Unknown Year")
            else:
                metadata = data["metadata"]
                ticker = metadata.get("ticker")
                cik = metadata.get("cik")
                year = metadata.get("year", "Unknown Year")
            text = data.get("cleaned_text", "")
            filing_type = data.get("filing_type", "10-K")
            metadata = {
                "ticker": ticker,
                "date": date,
                "cik": cik,
                "year": year,
                "filing_type": filing_type
            }
            # text = cut_text_10K(text)  # Cut to keep everything from "Item 1." onwards
            sections = split_sections2(text)
            processed_sections = process_sections2(sections)
            output_ticker_directory = output_directory / (ticker if ticker else "UNKNOWN_TICKER")
            output_ticker_directory.mkdir(exist_ok=True, parents=True)  # Ensure ticker directory exists
            if date: 
                output_file_path = output_ticker_directory / f"{year}_{date}.json"
            else:
                output_file_path = output_ticker_directory / f"{year}.json"
            output_data = {
                "metadata": metadata,
                "sections": processed_sections
            }
            with open(output_file_path, 'w', encoding='utf-8') as out_f:
                json.dump(output_data, out_f, ensure_ascii=False, indent=4)
            print(f"Processed and saved: {output_file_path}")
    except FileNotFoundError:
        print(f"File not found: {file_path}. Skipping.")
    except json.JSONDecodeError:
        print(f"Error decoding JSON from file: {file_path}. Skipping.")


Processed and saved: 10-K_sectioned_newer\A\2020_2020-12-18.json
Processed and saved: 10-K_sectioned_newer\A\2021_2021-12-17.json
Processed and saved: 10-K_sectioned_newer\A\2022_2022-12-21.json
Processed and saved: 10-K_sectioned_newer\A\2023_2023-12-20.json
Processed and saved: 10-K_sectioned_newer\A\2024_2024-12-20.json
Processed and saved: 10-K_sectioned_newer\AA\2021_2021-02-25.json
Processed and saved: 10-K_sectioned_newer\AA\2022_2022-02-24.json
Processed and saved: 10-K_sectioned_newer\AA\2023_2023-02-23.json
Processed and saved: 10-K_sectioned_newer\AA\2024_2024-02-21.json
Processed and saved: 10-K_sectioned_newer\AA\2025_2025-02-20.json
Processed and saved: 10-K_sectioned_newer\AACT\2024_2024-02-28.json
Processed and saved: 10-K_sectioned_newer\AACT\2025_2025-03-12.json
Processed and saved: 10-K_sectioned_newer\AAL\2021_2021-02-17.json
Processed and saved: 10-K_sectioned_newer\AAL\2022_2022-02-22.json
Processed and saved: 10-K_sectioned_newer\AAL\2023_2023-02-22.json
Processe

In [12]:
#10-q processing
import json, re, pathlib, textwrap

# ------------------------------------------------------------------
# 1. Configure what you consider “important”
#    (key = (Item header, keyword that must appear right after it))
# ------------------------------------------------------------------
TARGET_SECTIONS = {
    ('ITEM 1A', 'RISK')    : 'Risk Factors',
    ('ITEM 2',  'MANAGEMENT') : "MD&A (Management’s Discussion & Analysis)",
    ('ITEM 3',  'MARKET')  : 'Quant & Qualitative Market Risk'
}

HEADER_RE = re.compile(r'ITEM\s+(\d+[A-Z]?)\.', re.IGNORECASE)

def extract_sections_from_text(text: str,
                               targets: dict = TARGET_SECTIONS,
                               min_chars: int = 500,
                               max_digit_ratio: float = 0.40):
    """
    Return {friendly_name: section_text} for each target that passes the length
    and 'cleanliness' tests.  Non-matching or dirty sections are ignored.
    """
    # Locate every “ITEM <n>.” header
    matches = list(HEADER_RE.finditer(text))
    # results = {}
    sections = []

    for i, m in enumerate(matches):
        item_num = m.group(1).upper()
        lookahead = text[m.end(): m.end() + 120].upper()   # peek at header title

        # Check whether this header matches one of our targets
        for (item_key, keyword), friendly in targets.items():
            if item_key == f'ITEM {item_num}' and keyword in lookahead:
                start = m.end()
                end   = matches[i+1].start() if i+1 < len(matches) else len(text)
                chunk = text[start:end].strip()

                # Heuristic “junk” filters
                if len(chunk) >= min_chars:
                    digit_ratio = sum(c.isdigit() for c in chunk) / len(chunk)
                    if digit_ratio < max_digit_ratio:
                        #results[friendly] = chunk
                        hit = {
                            'item': item_num,
                            'section': friendly,
                            'text': chunk
                        }
                        sections.append(hit)
                break   # no need to test other targets for this header
    return sections

# ------------------------------------------------------------------
# 2. Driver – iterate over files and write out a trimmed JSON twin
# ------------------------------------------------------------------
def process_10q_files(paths, out_dir='10-Q_sectioned'):

    for p in paths:
        data = json.loads(pathlib.Path(p).read_text(encoding='utf-8'))
        sections = extract_sections_from_text(data['cleaned_text'])
        if sections:
            #drop the cleaned_text to save space
            ticker = data.get('ticker', 'UNKNOWN')
            year = data.get('year', 'UNKNOWN_YEAR')
            cik = data.get('cik', 'UNKNOWN_CIK')
            date = data.get('date', 'UNKNOWN_DATE')
            data['metadata'] = {
                'ticker': ticker,
                'year': year,
                'cik': cik,
                'date': date,
                'filing_type': '10-Q'
            }
            data.pop('ticker', None)  # Remove ticker from the main data
            data.pop('year', None)    # Remove year from the main data
            data.pop('cik', None)     # Remove cik from the main data
            data.pop('date', None)    # Remove date from the main data
            data.pop('filing_type', None)  # Remove filing_type from the main data
            data.pop('cleaned_text', None)  # Remove cleaned_text to save space
            data['sections'] = sections
            out_dir_path = pathlib.Path(out_dir) / f"{ticker}"
            out_dir_path.mkdir(parents=True, exist_ok=True)
            out_file = out_dir_path / f"{year}_{date}.json"
            with open(out_file, 'w', encoding='utf-8') as f:
                json.dump(data, f, ensure_ascii=False, indent=4)

        else:
            print(f"No target sections found in {p}. Skipping.")
            continue

# ------------------------------------------------------------------
# 3. Example call
# ------------------------------------------------------------------
if __name__ == "__main__":
    # sample_files = [
    #     'sec_filings_clean/AAL/10-Q/2020-04-30.json',
    #     'sec_filings_clean/ABCB/10-Q/2021-08-09.json'
    # ]
    directory = pathlib.Path('sec_filings_clean')
    sample_files = list(directory.glob('**/10-Q/*.json'))  # Adjust the path as needed

    process_10q_files(sample_files)


No target sections found in sec_filings_clean\AAMI\10-Q\2020-08-10.json. Skipping.
No target sections found in sec_filings_clean\AAMI\10-Q\2020-11-06.json. Skipping.
No target sections found in sec_filings_clean\AAMI\10-Q\2021-05-07.json. Skipping.
No target sections found in sec_filings_clean\AAMI\10-Q\2021-08-09.json. Skipping.
No target sections found in sec_filings_clean\AAMI\10-Q\2021-11-05.json. Skipping.
No target sections found in sec_filings_clean\AAMI\10-Q\2022-05-09.json. Skipping.
No target sections found in sec_filings_clean\AAMI\10-Q\2022-08-05.json. Skipping.
No target sections found in sec_filings_clean\AAMI\10-Q\2022-11-04.json. Skipping.
No target sections found in sec_filings_clean\AAMI\10-Q\2023-05-08.json. Skipping.
No target sections found in sec_filings_clean\AAMI\10-Q\2023-08-08.json. Skipping.
No target sections found in sec_filings_clean\AAMI\10-Q\2023-11-08.json. Skipping.
No target sections found in sec_filings_clean\AAMI\10-Q\2024-05-09.json. Skipping.
No t